In [ ]:
from netgen.csg import *
from ngsolve import *
from ngbem import *
import netgen.gui  # this opens up the netgen ui
import numpy as np
from ngsolve import Draw
import scipy
import matplotlib.pyplot as plt
from strayfield import stray_field
from General_Functions import MaximumMeshSize

In [ ]:
def MakeGeometry():  # this makes a box, with labelled faces
    geometry = CSGeometry()
    sphere = Sphere((0,0,0), 1)
    geometry.Add(sphere)
    return geometry

ngmesh = MakeGeometry().GenerateMesh(maxh=1/64)
mesh = Mesh(ngmesh)
Draw(mesh)
print(f"h_max = {MaximumMeshSize(mesh)}")  # ignore any warnings!
mesh.GetBoundaries()

In [ ]:
V = H1(mesh, order=1)
mag_gfu = CF((0, 0, 1)).Compile()
print(f"ndof = {V.ndof}")

In [ ]:
strayfield = stray_field(mag_gfu, mesh, order=2, check_error=True, exacu1=CF(z))

my_energy = -Integrate(0.5*InnerProduct(mag_gfu, strayfield), mesh, VOL)
stray_actual = CF((0,0,-1/3))
integrand = InnerProduct(strayfield - stray_actual, strayfield - stray_actual)
my_error = Integrate(integrand, mesh, VOL)

print(f"Calculated energy = {my_energy}, expected = {2*pi/9}, diff = {my_energy - 2*pi/9}")
print(f"L^2 error = {my_error}")